In [1]:
import pandas as pd
from clustergrammer2 import Network, CGM2, net
df = {}

>> clustergrammer2 backend version 0.14.0


In [2]:
# df['ini'] = pd.read_csv('https://raw.githubusercontent.com/nytimes/covid-19-data/master/us-states.csv')
df['ini'] = pd.read_csv('https://raw.githubusercontent.com/nytimes/covid-19-data/master/us-counties.csv')
df['ini'].shape

(279450, 6)

In [3]:
list_fips = df['ini']['fips'].value_counts().index.tolist()
list_fips = [int(x) for x in list_fips]

In [4]:
pd.DataFrame(list_fips).to_csv('fips.txt')

In [5]:
df['ini'].head()

date     county       state     fips  cases  deaths
0  2020-01-21  Snohomish  Washington  53061.0      1       0
1  2020-01-22  Snohomish  Washington  53061.0      1       0
2  2020-01-23  Snohomish  Washington  53061.0      1       0
3  2020-01-24       Cook    Illinois  17031.0      1       0
4  2020-01-24  Snohomish  Washington  53061.0      1       0

### Modify to start on March 1st 2020

In [6]:
df['mat'] = pd.DataFrame()
for inst_row in df['ini'].index.tolist():
    inst_date = df['ini'].loc[inst_row, 'date']
    inst_county = df['ini'].loc[inst_row, 'county']
    inst_cases = df['ini'].loc[inst_row, 'cases']
    
    df['mat'].loc[inst_county, inst_date] = inst_cases

# enforce date ordering    
dates = df['mat'].columns.tolist()
sorted(dates)
df['mat'] = df['mat'][dates]

# fill in missing value
net.load_df(df['mat'])
net.swap_nan_for_zero()
df['mat'] = net.export_df()

# calculate new cases in rolling 7 day window
list_ser = []
for inst_county in df['mat'].index.tolist():
    ser_county = df['mat'].loc[inst_county]
    ser_roll = ser_county.diff().rolling(7).mean()
#     ser_roll = ser_county.diff()
    list_ser.append(ser_roll)
    
df['diff'] = pd.concat(list_ser, axis=1).transpose()

# enforce date ordering
dates = df['diff'].columns.tolist()
sorted(dates)
df['diff'] = df['diff'][dates]

# get rid of nans
net.load_df(df['diff'])
net.swap_nan_for_zero()
df['diff'] = net.export_df()

# drop dates with no change
ser_date = df['diff'].sum(axis=0)
keep_dates = ser_date[ser_date > 0].index.tolist()
df['diff'] = df['diff'][keep_dates]

In [7]:
df['meta_county'] = pd.DataFrame()
for inst_row in df['ini'].index.tolist():
    inst_county = df['ini'].loc[inst_row, 'county']
    inst_state = df['ini'].loc[inst_row, 'state']    
    inst_fips = round(df['ini'].loc[inst_row, 'fips'])
    df['meta_county'].loc[inst_county, 'state'] = inst_state
    df['meta_county'].loc[inst_county, 'fips'] = inst_fips
df['meta_county'].shape

(1805, 2)

In [8]:
df['mat'].shape

(1805, 160)

In [9]:
# net.load_df(df['mat'])
# net.normalize(axis='row', norm_type='zscore')
# net.widget()

In [10]:
pops = net.load_json_to_dict('data/pops.json')

In [11]:
inst_fips

56045.0

In [12]:
pop_dict = {}
for inst_array in pops:
    inst_fips = int(inst_array[0])
    inst_pop = inst_array[1]
    pop_dict[inst_fips] = inst_pop

In [13]:
import numpy as np

In [14]:
for inst_county in df['meta_county'].index.tolist():
    inst_pop = 0
    inst_fips = df['meta_county'].loc[inst_county, 'fips']
    if np.isnan(inst_fips):
        # print(inst_fips)
        pass
    else:
        inst_fips = int(inst_fips)

        if inst_fips in pop_dict:
            inst_pop = pop_dict[inst_fips]
            

    df['meta_county'].loc[inst_county, 'Population'] = float(inst_pop/1000000)
        

In [15]:
df['meta_county'].loc['Bexar']

state           Texas
fips            48029
Population    1.98605
Name: Bexar, dtype: object

### Manually fix NYC (FIPs issue)

In [16]:
df['meta_county'].loc['New York City'] = 8

In [17]:
df['diff-norm'] = net.umi_norm(df['diff'].transpose()).transpose()

In [18]:
df['meta_county'] = df['meta_county'].astype(str)

In [19]:
df['meta_county'].head()

state     fips Population
Snohomish    Washington  53061.0   0.814901
Cook          Minnesota  27031.0   0.005393
Orange         Virginia  51137.0   0.036644
Maricopa        Arizona   4013.0   4.410824
Los Angeles  California   6037.0  10.105518

In [20]:
df['diff-proc'] = df['diff'][keep_dates]

In [21]:
ser_sum = df['diff'].sum(axis=1)/100000

In [22]:
df['meta_county']['Cases'] = ser_sum.astype(str)

In [23]:
net.load_df(df['diff-proc'])
net.normalize(axis='col', norm_type='umi')
df['diff-norm'] = net.export_df()

In [24]:
keep_dates_2 = df['diff-norm'].sum(axis=0)
keep_dates_2.min()

0.9999999999999741

In [25]:
df['diff-norm'][df['diff-norm'] > 0.5] = 0.5

In [26]:
net = Network(CGM2)
net.load_df(df['diff-proc'], meta_row=df['meta_county'], row_cats=['state', 'Population'])
df_tmp = net.export_df()
df_tmp = df_tmp.fillna(0)
df_tmp[df_tmp < 0] = 0

In [27]:
ser_max = df_tmp.max(axis=1)

In [28]:
df_norm = df_tmp.divide(ser_max, axis=0)

In [29]:
df_mid = df_norm - 0.5

In [30]:
net = Network(CGM2)
net.load_df(df_mid, meta_row=df['meta_county'], row_cats=['state', 'Population', 'Cases'])
# net.swap_nan_for_zero()
# net.normalize(axis='row', norm_type='zscore', z_clip=5)
# df['export'] = net.export_df()
net.widget()

CGM2(network='{"row_nodes": [{"name": "Snohomish", "ini": 1805, "clust": 31, "rank": 1618, "rankvar": 1114, "c…

In [31]:
# df['export'].to_csv('data/data_z-scored.csv')

In [32]:
df_mid.to_csv('data/data_mid.csv')

In [33]:
net.save_dict_to_json(net.viz, 'jsons/viz.json')

In [34]:
df['diff'].to_csv('data/data_diff.csv')

In [35]:
# net.load_df(df['diff'])
# net.normalize(axis='row', norm_type='zscore')
# net.widget()

In [36]:
# dates = df['mat'].columns.tolist()
# sorted(dates)

In [37]:
# from bqplot import *
# from ipywidgets import Layout

# import pandas as pd
# # county_data = pd.read_csv('us-counties.csv')
# county_data = pd.read_csv('https://raw.githubusercontent.com/nytimes/covid-19-data/master/us-counties.csv')
# county_data = county_data[county_data['fips'].notna()]
# county_data['fips'] = county_data['fips'].astype(int)
# county_data['date'] = pd.to_datetime(county_data['date'])

# total_county_data = county_data.groupby('fips')['deaths'].sum()
# total_county_data.index = total_county_data.index.astype(int)

# sc_geo_county = AlbersUSA()
# sc_c1_county = ColorScale()

# color_data_county = dict(zip(total_county_data.index, list(total_county_data)))

# map_styles_county = {'color': color_data_county,
#               'scales': {'projection': sc_geo_county, 'color': sc_c1_county}, 'colors': {'default_color': 'Grey'}}

# axis_county = ColorAxis(scale=sc_c1_county)

# county_map = Map(map_data=topo_load('map_data/USCountiesMap.json'), **map_styles_county)
# county_fig = Figure(marks=[county_map], axes=[axis_county],title='US Elections 2008 - Example',
#                     layout=Layout(min_width='800px', min_height='550px'))



In [38]:
# total_county_data.head()

In [39]:
# date_sc = DateScale()
# count_sc_y = LinearScale(max=np.float(county_data.deaths.max()))

# date_ax = Axis(scale=date_sc, label='Date')
# count_ax = Axis(scale=count_sc_y, orientation='vertical', label='Deaths')

# date_count = Lines(scales={'x': date_sc, 'y': count_sc_y})

# bar_fig = Figure(marks=[date_count], axes=[date_ax, count_ax],
#                  layout=Layout(min_width='600px', min_height='400px'))

# def tooltip_function(name, value):
#     state = value['data']['id']
#     count_choice = county_data[county_data['fips'] == state]
#     state_name = count_choice['state'].iloc[0]
#     county_name = count_choice['county'].iloc[0]
#     date_count.x = count_choice['date']
#     date_count.y = count_choice['deaths']
#     bar_fig.title = f'{county_name} {state_name}'

In [40]:
# county_fig